# Проект: линейная регрессия

Проект: Создание модели линейной регрессии для прогнозирования цены за квадратный метр квартиры и определения наиболее значимых факторов

### __Цель:__

Разработать модель линейной регрессии, которая будет точно предсказывать цену за квадратный метр квартиры на основе различных характеристик квартиры.

### __Задачи:__

- Собрать и подготовить набор данных, содержащий информацию о ценах на квартиры и соответствующих характеристиках.
- Провести анализ данных, чтобы выявить корреляции между характеристиками и ценами на квартиры.
- Создать модель линейной регрессии, используя выбранные характеристики в качестве независимых переменных и цену за квадратный метр в качестве зависимой переменной.
- Оценить производительность модели с помощью показателей, таких как коэффициент детерминации (R²)
- Оптимизировать модель для улучшения ее точности и надежности.

## Подготовка

Этот этап включает в себя импортрование нужных библиотек, загрузку и предобработку данных

In [128]:
import json
import pandas as pd
import folium

import statsmodels.api as sm
import statsmodels.formula.api as smf 

import plotly.express as px
import seaborn as sns

import math

from IPython.display import display, HTML
display(HTML("<style>.container { width:80% !important; }</style>"))

In [129]:
data = pd.read_csv('real_estate_data.csv', index_col=0) # можно залить на гитхаб, обращаться к ссылке
data.head()

author              author_type  \
0  TEN девелопмент                developer   
1  AVS Девелопмент  official_representative   
2  TEN девелопмент                developer   
3      DREAM ROOMS        real_estate_agent   
4   Первостроитель                developer   

                                        url      location deal_type  \
0  https://ekb.cian.ru/sale/flat/298036657/  Екатеринбург      sale   
1  https://ekb.cian.ru/sale/flat/300540252/  Екатеринбург      sale   
2  https://ekb.cian.ru/sale/flat/298833689/  Екатеринбург      sale   
3  https://ekb.cian.ru/sale/flat/300484825/  Екатеринбург      sale   
4  https://ekb.cian.ru/sale/flat/297114703/  Екатеринбург      sale   

  accommodation_type  floor  floors_count  rooms_count  total_meters  ...  \
0               flat     19            31            1          46.6  ...   
1               flat      3            24            1          43.0  ...   
2               flat     16            25            1          37.3  ...   
3               flat      2            17            1          39.7  ...   
4               flat      2            24            1          30.6  ...   

     underground      residential_complex  \
0     Чкаловская           Дом на Бардина   
1  Геологическая                  RedRock   
2     Чкаловская            Ботаника LIFE   
3  Геологическая                      NaN   
4  Геологическая  Проспект Мира. Компаунд   

                        unique_address                             LAT_LON  \
0  Екатеринбург, Академика Бардина,26А  (56.807174592523, 60.557521651104)   
1          Екатеринбург, Большакова,66  (56.818997938835, 60.615136587595)   
2           Екатеринбург, 8 Марта,204Д  (56.796060105225, 60.609919382543)   
3            Екатеринбург, Викулова,55  (56.823800013784, 60.544489994899)   
4              Екатеринбург, Мира,47/7   (56.833271681853, 60.65788143617)   

            underground_search                             metro_address  \
0     Станция метро Чкаловская     Екатеринбург,Станция метро Чкаловская   
1  Станция метро Геологическая  Екатеринбург,Станция метро Геологическая   
2     Станция метро Чкаловская     Екатеринбург,Станция метро Чкаловская   
3  Станция метро Геологическая  Екатеринбург,Станция метро Геологическая   
4  Станция метро Геологическая  Екатеринбург,Станция метро Геологическая   

                  LAT_LON_metro metro_nearest airport_nearest center_distance  
0  ('56.8073485', '60.6098317')   3195.470643    16635.129692     4560.916391  
1  ('56.8264026', '60.6036815')   1081.266957    14224.872426     1847.788917  
2  ('56.8073485', '60.6098317')   1257.045490    13210.026400     4389.911054  
3  ('56.8264026', '60.6036815')   3625.656706    18175.196617     4293.618449  
4  ('56.8264026', '60.6036815')   3396.130722    13307.635663     2840.590357  

[5 rows x 29 columns]

In [130]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1153 entries, 0 to 1152
Data columns (total 29 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   author                1135 non-null   object 
 1   author_type           1135 non-null   object 
 2   url                   1153 non-null   object 
 3   location              1153 non-null   object 
 4   deal_type             1153 non-null   object 
 5   accommodation_type    1153 non-null   object 
 6   floor                 1153 non-null   int64  
 7   floors_count          1153 non-null   int64  
 8   rooms_count           1153 non-null   int64  
 9   total_meters          1153 non-null   float64
 10  price                 1153 non-null   int64  
 11  year_of_construction  1153 non-null   int64  
 12  house_material_type   1153 non-null   object 
 13  living_meters         1153 non-null   float64
 14  kitchen_meters        1153 non-null   float64
 15  phone                 1153

## Обработка данных

### Удаление ненужных столбцов

In [131]:
data.columns

Index(['author', 'author_type', 'url', 'location', 'deal_type',
       'accommodation_type', 'floor', 'floors_count', 'rooms_count',
       'total_meters', 'price', 'year_of_construction', 'house_material_type',
       'living_meters', 'kitchen_meters', 'phone', 'district', 'street',
       'house_number', 'underground', 'residential_complex', 'unique_address',
       'LAT_LON', 'underground_search', 'metro_address', 'LAT_LON_metro',
       'metro_nearest', 'airport_nearest', 'center_distance'],
      dtype='object')

In [132]:
for i in ['phone', 'author', 'url',
                  'deal_type', 'accommodation_type',
                  'house_material_type', 'street',
                  'house_number', 'metro_address',
                  'underground_search', 'unique_address']:
    print(i, end=', ')

phone, author, url, deal_type, accommodation_type, house_material_type, street, house_number, metro_address, underground_search, unique_address, 

In [133]:
data = data.drop(['phone', 'author', 'url',
                  'deal_type', 'accommodation_type',
                  'house_material_type', 'street',
                  'house_number', 'metro_address',
                  'underground_search', 'unique_address'], axis=1)

Удалив ненужные столбцы, располагаем следующими данными:

In [134]:
data

author_type      location  floor  floors_count  rooms_count  \
0                   developer  Екатеринбург     19            31            1   
1     official_representative  Екатеринбург      3            24            1   
2                   developer  Екатеринбург     16            25            1   
3           real_estate_agent  Екатеринбург      2            17            1   
4                   developer  Екатеринбург      2            24            1   
...                       ...           ...    ...           ...          ...   
1148        real_estate_agent  Екатеринбург      1             5            1   
1149        real_estate_agent  Екатеринбург      1             3            1   
1150                homeowner  Екатеринбург      2             9            3   
1151                homeowner  Екатеринбург      2             5            3   
1152                homeowner  Екатеринбург      1             2            2   

      total_meters    price  year_of_construction  living_meters  \
0             46.6  7738000                  2023      16.800000   
1             43.0  9035000                  2024      13.000000   
2             37.3  7874000                  2023      12.000000   
3             39.7  4300000                  1990      21.400000   
4             30.6  7367000                  2023      16.000000   
...            ...      ...                   ...            ...   
1148          16.0  1910000                  1974       5.842568   
1149          17.1  2850000                  1961       8.200000   
1150          58.2  6500000                  1981      51.300000   
1151          58.5  5700000                  1972      21.361889   
1152          55.4  4600000                  1959      34.700000   

      kitchen_meters       district       underground  \
0          13.800000      Ленинский        Чкаловская   
1          16.900000          Центр     Геологическая   
2          15.500000     Чкаловский        Чкаловская   
3           9.200000  Верх-Исетский     Геологическая   
4           5.000000      Кировский     Геологическая   
...              ...            ...               ...   
1148        5.000000     Чкаловский      Ботаническая   
1149        3.900000      Кировский  Машиностроителей   
1150        4.000000      Кировский            Динамо   
1151       10.332988      Кировский  Машиностроителей   
1152       10.000000      Кировский         Уральская   

          residential_complex                             LAT_LON  \
0              Дом на Бардина  (56.807174592523, 60.557521651104)   
1                     RedRock  (56.818997938835, 60.615136587595)   
2               Ботаника LIFE  (56.796060105225, 60.609919382543)   
3                         NaN  (56.823800013784, 60.544489994899)   
4     Проспект Мира. Компаунд   (56.833271681853, 60.65788143617)   
...                       ...                                 ...   
1148                      NaN  (56.756301385703, 60.609313035668)   
1149                      NaN  (56.854232355877, 60.666780090157)   
1150                      NaN  (56.849415593707, 60.625409266764)   
1151                      NaN  (56.863764059551, 60.639506874458)   
1152                      NaN   (56.85765540081, 60.626531811723)   

                     LAT_LON_metro  metro_nearest  airport_nearest  \
0     ('56.8073485', '60.6098317')    3195.470643     16635.129692   
1     ('56.8264026', '60.6036815')    1081.266957     14224.872426   
2     ('56.8073485', '60.6098317')    1257.045490     13210.026400   
3     ('56.8264026', '60.6036815')    3625.656706     18175.196617   
4     ('56.8264026', '60.6036815')    3396.130722     13307.635663   
...                            ...            ...              ...   
1148    ('56.797543', '60.631804')    4793.915264     12042.736161   
1149   ('56.8784313', '60.612468')    4270.148693     14791.040672   
1150   ('56.847786', '60.6015868')    1464.900501     15974.293611   
1151   ('56.87

### Создание dummy-переменных

Создадим dummy-переменные с ближайшей станцией метро и районом и типом владельца

In [135]:
dummy_owner = pd.get_dummies(data['author_type'])
dummy_owner

developer  homeowner  official_representative  real_estate_agent  \
0          True      False                    False              False   
1         False      False                     True              False   
2          True      False                    False              False   
3         False      False                    False               True   
4          True      False                    False              False   
...         ...        ...                      ...                ...   
1148      False      False                    False               True   
1149      False      False                    False               True   
1150      False       True                    False              False   
1151      False       True                    False              False   
1152      False       True                    False              False   

      realtor  representative_developer  unknown  
0       False                     False    False  
1       False                     False    False  
2       False                     False    False  
3       False                     False    False  
4       False                     False    False  
...       ...                       ...      ...  
1148    False                     False    False  
1149    False                     False    False  
1150    False                     False    False  
1151    False                     False    False  
1152    False                     False    False  

[1153 rows x 7 columns]

In [136]:
developer = dummy_owner['developer'] | dummy_owner['official_representative'] | dummy_owner['representative_developer'] 
realtor = dummy_owner['real_estate_agent'] | dummy_owner['realtor']

In [137]:
data['is_developer'] = developer
data['realtor'] = realtor

In [138]:
dummy_metro = pd.get_dummies(data['underground']).astype(int)
dummy_metro.columns = list(map(lambda x: 'Метро_'+x.replace(' ', '').replace('-', '_').lower(), dummy_metro.columns))
display(dummy_metro.head())

dummy_district = pd.get_dummies(data['district']).astype(int)
dummy_district.columns = list(map(lambda x: 'Район_'+x.replace(' ', '').replace('-', '_').lower(), dummy_district.columns))
display(dummy_district.head())

Метро_ботаническая  Метро_геологическая  Метро_динамо  \
0                   0                    0             0   
1                   0                    1             0   
2                   0                    0             0   
3                   0                    1             0   
4                   0                    1             0   

   Метро_машиностроителей  Метро_площадь1905года  Метро_проспекткосмонавтов  \
0                       0                      0                          0   
1                       0                      0                          0   
2                       0                      0                          0   
3                       0                      0                          0   
4                       0                      0                          0   

   Метро_уралмаш  Метро_уральская  Метро_чкаловская  
0              0                0                 1  
1              0                0                 0  
2              0                0                 1  
3              0                0                 0  
4              0                0                 0

Район_верх_исетский  Район_железнодорожный  Район_кировский  \
0                    0                      0                0   
1                    0                      0                0   
2                    0                      0                0   
3                    1                      0                0   
4                    0                      0                1   

   Район_ленинский  Район_октябрьский  Район_орджоникидзевский  Район_центр  \
0                1                  0                        0            0   
1                0                  0                        0            1   
2                0                  0                        0            0   
3                0                  0                        0            0   
4                0                  0                        0            0   

   Район_чкаловский  
0                 0  
1                 0  
2                 1  
3                 0  
4                 0

In [139]:
# присоединяем дамми-переменные

data = pd.concat([data, dummy_metro], axis=1)
data = pd.concat([data, dummy_district], axis=1)

data.head()

author_type      location  floor  floors_count  rooms_count  \
0                developer  Екатеринбург     19            31            1   
1  official_representative  Екатеринбург      3            24            1   
2                developer  Екатеринбург     16            25            1   
3        real_estate_agent  Екатеринбург      2            17            1   
4                developer  Екатеринбург      2            24            1   

   total_meters    price  year_of_construction  living_meters  kitchen_meters  \
0          46.6  7738000                  2023           16.8            13.8   
1          43.0  9035000                  2024           13.0            16.9   
2          37.3  7874000                  2023           12.0            15.5   
3          39.7  4300000                  1990           21.4             9.2   
4          30.6  7367000                  2023           16.0             5.0   

   ... Метро_уральская Метро_чкаловская Район_верх_исетский  \
0  ...               0                1                   0   
1  ...               0                0                   0   
2  ...               0                1                   0   
3  ...               0                0                   1   
4  ...               0                0                   0   

  Район_железнодорожный Район_кировский  Район_ленинский  Район_октябрьский  \
0                     0               0                1                  0   
1                     0               0                0                  0   
2                     0               0                0                  0   
3                     0               0                0                  0   
4                     0               1                0                  0   

   Район_орджоникидзевский  Район_центр  Район_чкаловский  
0                        0            0                 0  
1                        0            1                 0  
2                        0            0                 1  
3                        0            0                 0  
4                        0            0                 0  

[5 rows x 37 columns]

In [140]:
numeric_cols = ['floor', 'floors_count', 'rooms_count', 'total_meters', 'price',
       'year_of_construction', 'living_meters', 'kitchen_meters',
       'metro_nearest', 'airport_nearest', 'center_distance'] # cохраним в отдельном списке числовые значения

### Очистка выбросов

In [141]:
# удалим выбросы:
# по каждому числовому столбцу оставим только значения в диапазоне
# от 1-го перцентиля до 99-го

for col in data[numeric_cols]:
    lower_threshold = data[col].quantile(.01)
    upper_threshold = data[col].quantile(.99)
    
    data = data[data[col] >= lower_threshold]
    data = data[data[col] <= upper_threshold]

In [142]:
data # данные после очистки

author_type      location  floor  floors_count  rooms_count  \
0                   developer  Екатеринбург     19            31            1   
1     official_representative  Екатеринбург      3            24            1   
2                   developer  Екатеринбург     16            25            1   
3           real_estate_agent  Екатеринбург      2            17            1   
4                   developer  Екатеринбург      2            24            1   
...                       ...           ...    ...           ...          ...   
1146        real_estate_agent  Екатеринбург     10            16            1   
1147                homeowner  Екатеринбург      6             9            1   
1149        real_estate_agent  Екатеринбург      1             3            1   
1150                homeowner  Екатеринбург      2             9            3   
1151                homeowner  Екатеринбург      2             5            3   

      total_meters    price  year_of_construction  living_meters  \
0             46.6  7738000                  2023      16.800000   
1             43.0  9035000                  2024      13.000000   
2             37.3  7874000                  2023      12.000000   
3             39.7  4300000                  1990      21.400000   
4             30.6  7367000                  2023      16.000000   
...            ...      ...                   ...            ...   
1146          25.0  3690000                  2023      10.000000   
1147          72.0  9900000                  1977      26.291555   
1149          17.1  2850000                  1961       8.200000   
1150          58.2  6500000                  1981      51.300000   
1151          58.5  5700000                  1972      21.361889   

      kitchen_meters  ... Метро_уральская Метро_чкаловская  \
0          13.800000  ...               0                1   
1          16.900000  ...               0                0   
2          15.500000  ...               0                1   
3           9.200000  ...               0                0   
4           5.000000  ...               0                0   
...              ...  ...             ...              ...   
1146        5.000000  ...               0                0   
1147       12.717524  ...               0                0   
1149        3.900000  ...               0                0   
1150        4.000000  ...               0                0   
1151       10.332988  ...               0                0   

     Район_верх_исетский Район_железнодорожный Район_кировский  \
0                      0                     0               0   
1                      0                     0               0   
2                      0                     0               0   
3                      1                     0               0   
4                      0                     0               1   
...                  ...                   ...             ...   
1146                   0                     0               0   
1147                   0                     0               1   
1149                   0                     0               1   
1150                   0                     0               1   
1151                   0                     0               1   

      Район_ленинский  Район_октябрьский  Район_орджоникидзевский  \
0                   1                  0                        0   
1                   0                  0                        0   
2                   0                  0                        0   
3                   0                  0                        0   
4                   0                  0                        0   
...               ...                ...                      ...   
1146                0                  0                        0   
1147                0                  0                        0   
1149                0                  0                        0   


In [143]:
for i in numeric_cols:
    px.box(data[i], title=f'Распределение переменной {i} - boxplot').show()

## Описательная статистика данных и корелляции

In [148]:
data['price_per_sq_meter'] = data['price']/data['total_meters']  # создание целевой переменной

In [149]:
print('Описательная статистика по числовым столбцам')
data[['price_per_sq_meter']+numeric_cols].describe()

Описательная статистика по числовым столбцам


price_per_sq_meter       floor  floors_count  rooms_count  \
count          964.000000  964.000000    964.000000   964.000000   
mean        137507.464762    7.963693     17.048755     2.020747   
std          39057.589359    6.501196      8.230752     1.071477   
min          68771.138670    1.000000      3.000000     1.000000   
25%         109921.630094    3.000000      9.000000     1.000000   
50%         131950.000000    6.000000     17.000000     2.000000   
75%         157136.195737   11.000000     25.000000     3.000000   
max         299906.832298   27.000000     32.000000     5.000000   

       total_meters         price  year_of_construction  living_meters  \
count    964.000000  9.640000e+02            964.000000     964.000000   
mean      56.470425  7.659593e+06           2009.942946      26.792892   
std       26.721844  4.261068e+06             20.564158      15.434125   
min       17.000000  2.250000e+06           1953.000000       7.120630   
25%       35.110000  4.749732e+06           1996.750000      14.770742   
50%       52.450000  6.590000e+06           2022.000000      22.401298   
75%       71.350000  9.529630e+06           2024.000000      37.075000   
max      188.000000  2.850000e+07           2026.000000      80.000000   

       kitchen_meters  metro_nearest  airport_nearest  center_distance  
count      964.000000     964.000000       964.000000       964.000000  
mean        11.412559    3839.003180     15802.603477      5693.852885  
std          6.335124    2368.074003      4155.931420      2552.711386  
min          3.000000     358.123386      4856.708605      1065.120936  
25%          6.261173    1611.740855     13330.600799      3592.190427  
50%          9.783662    3554.872611     16478.483431      5621.623982  
75%         15.400000    5580.504180     18709.944069      7413.140718  
max         35.000000   13074.674294     23868.139941     11965.145535

In [150]:
print('Медианная цена квартиры', data['price'].median(), 'рублей')

Медианная цена квартиры 6590000.0 рублей


- Средняя цена квадратного метра в нашей выборке – 137507 рублей
- Квартиры в среднем расположены на 7,96 ~ 8 этаже
- В доме в среднем 17 этажей
- В среднем в квартире 2 комнаты
- Средняя площадь квартиры 56,5 кв. метров
- Медианная цена квартиры 6 590 000
- Средний год постройки зданий 2009.94 ~ 2010
- Среднее расстояние до метро 3839 метров
- Среднее расстояние до аэропорта 15802 метра
- Среднее расстояние до центра 5693
- Четверть всех наблюдений зарегистрирована из Чкаловского района
- Меньше всего наблюдений из Центрального района – всего 3,57%
- Самая дорогая цена квадрата – в центральном районе. Самый дешевый квадратный метр – в Железнодорожном районе
- Застройщик и официальные представители в среднем запрашивают более высокую цену за квадратный метр жилья


In [151]:
corr = data[['price_per_sq_meter']+numeric_cols].corr()

cmap = sns.color_palette("rocket_r", as_cmap=True)

corr.style.background_gradient(cmap, axis=1)\
    .format(precision=3)\
    .set_properties(**{'max-width': '80px', 'font-size': '10pt'})\
    .set_caption("Матрица корреляции (тепловая карта)")

Обнаружена сильная (> 0.7) корреляция в следующих парах переменных:
- __total_meters__ и __living_meters__
- __year_of_construction__ и __floors_count__
- __living_meters__ и __rooms_count__

### Гистограммы

In [152]:
fig = px.histogram(data['price_per_sq_meter'], title = 'Распределение переменной '+'price_per_sq_meter')
fig.update_layout(showlegend=False)
fig.add_vline(data['price_per_sq_meter'].mean(),
              annotation_text="Среднее значение = " + str(round(data['price_per_sq_meter'].mean(), 3)),
              line_color="red")
fig.add_vline(data['price_per_sq_meter'].median(),
              annotation_text="Медианное значение = " + str(round(data['price_per_sq_meter'].median(), 3)),
              line_color="green",
             annotation_position="left")
fig.show()

In [153]:
for col in data[numeric_cols].columns:
    fig = px.histogram(data[col], title = 'Распределение переменной '+col)
    fig.update_layout(showlegend=False)
    fig.add_vline(data[col].mean(),
                  annotation_text="Среднее значение = " + str(round(data[col].mean(), 3)),
                  line_color="red")
    fig.add_vline(data[col].median(),
                  annotation_text="Медианное значение = " + str(round(data[col].median(), 3)),
                  line_color="green",
                 annotation_position="left")
    fig.show()

### Scatter-диаграммы

In [154]:
import time
for col in data[numeric_cols].columns:
    fig = px.scatter(data,
                     y='price_per_sq_meter',
                     x=col,
                     trendline='ols',
                     title='График взаимного распределения цены за кв.метр и переменной '+col)
    fig.show()
    time.sleep(1)

### Различные визуализации

In [155]:
data

author_type      location  floor  floors_count  rooms_count  \
0                   developer  Екатеринбург     19            31            1   
1     official_representative  Екатеринбург      3            24            1   
2                   developer  Екатеринбург     16            25            1   
3           real_estate_agent  Екатеринбург      2            17            1   
4                   developer  Екатеринбург      2            24            1   
...                       ...           ...    ...           ...          ...   
1146        real_estate_agent  Екатеринбург     10            16            1   
1147                homeowner  Екатеринбург      6             9            1   
1149        real_estate_agent  Екатеринбург      1             3            1   
1150                homeowner  Екатеринбург      2             9            3   
1151                homeowner  Екатеринбург      2             5            3   

      total_meters    price  year_of_construction  living_meters  \
0             46.6  7738000                  2023      16.800000   
1             43.0  9035000                  2024      13.000000   
2             37.3  7874000                  2023      12.000000   
3             39.7  4300000                  1990      21.400000   
4             30.6  7367000                  2023      16.000000   
...            ...      ...                   ...            ...   
1146          25.0  3690000                  2023      10.000000   
1147          72.0  9900000                  1977      26.291555   
1149          17.1  2850000                  1961       8.200000   
1150          58.2  6500000                  1981      51.300000   
1151          58.5  5700000                  1972      21.361889   

      kitchen_meters  ... Метро_чкаловская Район_верх_исетский  \
0          13.800000  ...                1                   0   
1          16.900000  ...                0                   0   
2          15.500000  ...                1                   0   
3           9.200000  ...                0                   1   
4           5.000000  ...                0                   0   
...              ...  ...              ...                 ...   
1146        5.000000  ...                0                   0   
1147       12.717524  ...                0                   0   
1149        3.900000  ...                0                   0   
1150        4.000000  ...                0                   0   
1151       10.332988  ...                0                   0   

     Район_железнодорожный Район_кировский Район_ленинский  Район_октябрьский  \
0                        0               0               1                  0   
1                        0               0               0                  0   
2                        0               0               0                  0   
3                        0               0               0                  0   
4                        0               1               0                  0   
...                    ...             ...             ...                ...   
1146                     0               0               0                  0   
1147                     0               1               0                  0   
1149                     0               1               0                  0   
1150                     0               1               0                  0   
1151                     0               1               0                  0   

      Район_орджоникидзевский  Район_центр  Район_чкаловский  \
0                           0            0                 0   
1                           0            1                 0   
2                           0            0                 1   
3                           0            0                 0   
4                           0            0                 0   
...                       ...          ...               ...   
1146          

In [156]:
ekb_lat, ekb_lng = 56.82975861474145, 60.62175014660637

Наблюдения (объекты) на карте Екатеринбурга

In [157]:
# импортируем карту и маркер
from folium import Map, Marker
# импортируем кластер
from folium.plugins import MarkerCluster
m = Map(location=[ekb_lat, ekb_lng], zoom_start=12)
# создаём пустой кластер, добавляем его на карту
marker_cluster = MarkerCluster().add_to(m)

# пишем функцию, которая принимает строку датафрейма,
# создаёт маркер в текущей точке и добавляет его в кластер marker_cluster
def create_clusters(row):
    Marker(
        [eval(row['LAT_LON'])[0],
         eval(row['LAT_LON'])[1]],
        popup=f"Цена: {row['price']}",
    ).add_to(marker_cluster)

# применяем функцию create_clusters() к каждой строке датафрейма
data.apply(create_clusters, axis=1)

# выводим карту
m

In [158]:
median_price_by_districts = data.groupby('district', as_index=False)['price'].median().sort_values(by='price', ascending=False)
median_price_by_districts

district       price
6              Центр  15507000.0
2          Кировский   7829915.0
0      Верх-Исетский   7020000.0
3          Ленинский   6500000.0
5  Орджоникидзевский   5990000.0
1    Железнодорожный   5800000.0
4        Октябрьский   5797000.0
7         Чкаловский   5550000.0

In [159]:
fig = px.bar(median_price_by_districts, x='district', y='price', text='price', title='Медианная цена объекта по районам')
fig.add_hline(data['price'].median(), annotation_text=f"Медианная цена по всем наблюдениям: {data['price'].median()}")
fig.show()

In [160]:
median_price_sq_by_districts = data.groupby('district', as_index=False)['price_per_sq_meter'].median().sort_values(by='price_per_sq_meter', ascending=False)
median_price_sq_by_districts['price_per_sq_meter'] = median_price_sq_by_districts['price_per_sq_meter'].apply(round) 
fig = px.bar(median_price_sq_by_districts, x='district', y='price_per_sq_meter', text='price_per_sq_meter', title='Медианная цена/кв.метр объекта по районам')
fig.add_hline(data['price_per_sq_meter'].median(), annotation_text=f"Медианная цена за кв.метр по всем наблюдениям: {data['price_per_sq_meter'].median()}")
fig.show()

In [161]:
data

author_type      location  floor  floors_count  rooms_count  \
0                   developer  Екатеринбург     19            31            1   
1     official_representative  Екатеринбург      3            24            1   
2                   developer  Екатеринбург     16            25            1   
3           real_estate_agent  Екатеринбург      2            17            1   
4                   developer  Екатеринбург      2            24            1   
...                       ...           ...    ...           ...          ...   
1146        real_estate_agent  Екатеринбург     10            16            1   
1147                homeowner  Екатеринбург      6             9            1   
1149        real_estate_agent  Екатеринбург      1             3            1   
1150                homeowner  Екатеринбург      2             9            3   
1151                homeowner  Екатеринбург      2             5            3   

      total_meters    price  year_of_construction  living_meters  \
0             46.6  7738000                  2023      16.800000   
1             43.0  9035000                  2024      13.000000   
2             37.3  7874000                  2023      12.000000   
3             39.7  4300000                  1990      21.400000   
4             30.6  7367000                  2023      16.000000   
...            ...      ...                   ...            ...   
1146          25.0  3690000                  2023      10.000000   
1147          72.0  9900000                  1977      26.291555   
1149          17.1  2850000                  1961       8.200000   
1150          58.2  6500000                  1981      51.300000   
1151          58.5  5700000                  1972      21.361889   

      kitchen_meters  ... Метро_чкаловская Район_верх_исетский  \
0          13.800000  ...                1                   0   
1          16.900000  ...                0                   0   
2          15.500000  ...                1                   0   
3           9.200000  ...                0                   1   
4           5.000000  ...                0                   0   
...              ...  ...              ...                 ...   
1146        5.000000  ...                0                   0   
1147       12.717524  ...                0                   0   
1149        3.900000  ...                0                   0   
1150        4.000000  ...                0                   0   
1151       10.332988  ...                0                   0   

     Район_железнодорожный Район_кировский Район_ленинский  Район_октябрьский  \
0                        0               0               1                  0   
1                        0               0               0                  0   
2                        0               0               0                  0   
3                        0               0               0                  0   
4                        0               1               0                  0   
...                    ...             ...             ...                ...   
1146                     0               0               0                  0   
1147                     0               1               0                  0   
1149                     0               1               0                  0   
1150                     0               1               0                  0   
1151                     0               1               0                  0   

      Район_орджоникидзевский  Район_центр  Район_чкаловский  \
0                           0            0                 0   
1                           0            1                 0   
2                           0            0                 1   
3                           0            0                 0   
4                           0            0                 0   
...                       ...          ...               ...   
1146          

In [162]:
median_price_sq_by_districts = data.groupby('author_type', as_index=False)['price_per_sq_meter'].median().sort_values(by='price_per_sq_meter', ascending=False)
median_price_sq_by_districts['price_per_sq_meter'] = median_price_sq_by_districts['price_per_sq_meter'].apply(round) 
fig = px.bar(median_price_sq_by_districts, x='author_type', y='price_per_sq_meter', text='price_per_sq_meter', title='Медианная цена/кв.метр объекта по типу продавца')
fig.add_hline(data['price_per_sq_meter'].median(), annotation_text=f"Медианная цена за кв.метр по всем наблюдениям: {data['price_per_sq_meter'].median()}")
fig.show()

In [163]:
observations_by_districts = data.groupby('district', as_index=False)['price_per_sq_meter'].count().sort_values(by='price_per_sq_meter', ascending=False)
observations_by_districts

district  price_per_sq_meter
7         Чкаловский                 201
2          Кировский                 133
0      Верх-Исетский                 119
5  Орджоникидзевский                 105
4        Октябрьский                  79
3          Ленинский                  65
1    Железнодорожный                  55
6              Центр                  28

In [164]:
fig = px.pie(observations_by_districts, values='price_per_sq_meter', names='district', title='Доля наблюдений из разных районов')
fig.update_traces(textposition='inside', textinfo='percent+label')
fig.update_layout(showlegend=False)
fig.show()

In [165]:
seller_type = pd.DataFrame({'Тип продавца':['Застройщик', 'Риэлтор', 'Иной'], 'Количество объектов':[data['is_developer'].sum(), data['realtor'].sum(), data.shape[0] - data['realtor'].sum() - data['is_developer'].sum()]})

In [166]:
seller_type

Тип продавца  Количество объектов
0   Застройщик                  398
1      Риэлтор                  487
2         Иной                   79

In [167]:
fig = px.pie(seller_type, values='Количество объектов', names='Тип продавца', title='Доля наблюдений по типу продавца')
fig.update_traces(textposition='inside', textinfo='percent+label')
fig.update_layout(showlegend=False)
fig.show()


## Преобразования  и дополнительные переменные

In [168]:
data['log_center_distance'] = data['center_distance'].apply(math.log) # переменная "расстояние до центра" пЫодходит для логарифмирования

In [169]:
px.scatter(data,
           y='price_per_sq_meter',
           x='log_center_distance',
           trendline='ols', title='Переменная center_distance после логарифмирования')

In [170]:
data['is_last_floor'] = (data['floor']==data['floors_count']).astype(int)
data['is_first_floor'] = (data['floor']==1).astype(int)

In [171]:
data['is_residential_complex'] = (~data['residential_complex'].isna()).astype(int)

In [172]:
data['part_of_kitchen'] = data['kitchen_meters'] / data['total_meters']

In [173]:
data['part_of_living'] = data['living_meters'] / data['total_meters']

In [174]:
regression_cols = numeric_cols + ['Метро_ботаническая', 'Метро_геологическая',
       'Метро_динамо', 'Метро_машиностроителей', 'Метро_площадь1905года',
       'Метро_проспекткосмонавтов', 'Метро_уралмаш', 'Метро_уральская',
       'Метро_чкаловская', 'Район_верх_исетский', 'Район_железнодорожный',
       'Район_кировский', 'Район_ленинский', 'Район_октябрьский',
       'Район_орджоникидзевский', 'Район_центр', 'Район_чкаловский',
       'price_per_sq_meter', 'log_center_distance', 'is_last_floor',
       'is_first_floor', 'is_residential_complex', 'part_of_kitchen',
       'part_of_living']

In [175]:
for i in numeric_cols + ['Метро_ботаническая', 'Метро_геологическая',
       'Метро_динамо', 'Метро_машиностроителей', 'Метро_площадь1905года',
       'Метро_проспекткосмонавтов', 'Метро_уралмаш', 'Метро_уральская',
       'Метро_чкаловская', 'Район_верх_исетский', 'Район_железнодорожный',
       'Район_кировский', 'Район_ленинский', 'Район_октябрьский',
       'Район_орджоникидзевский', 'Район_центр', 'Район_чкаловский',
       'price_per_sq_meter', 'log_center_distance', 'is_last_floor',
       'is_first_floor', 'is_residential_complex', 'part_of_kitchen',
       'part_of_living']:
    print('data.'+i+' + ', end='')

data.floor + data.floors_count + data.rooms_count + data.total_meters + data.price + data.year_of_construction + data.living_meters + data.kitchen_meters + data.metro_nearest + data.airport_nearest + data.center_distance + data.Метро_ботаническая + data.Метро_геологическая + data.Метро_динамо + data.Метро_машиностроителей + data.Метро_площадь1905года + data.Метро_проспекткосмонавтов + data.Метро_уралмаш + data.Метро_уральская + data.Метро_чкаловская + data.Район_верх_исетский + data.Район_железнодорожный + data.Район_кировский + data.Район_ленинский + data.Район_октябрьский + data.Район_орджоникидзевский + data.Район_центр + data.Район_чкаловский + data.price_per_sq_meter + data.log_center_distance + data.is_last_floor + data.is_first_floor + data.is_residential_complex + data.part_of_kitchen + data.part_of_living + 

## Модели регрессии

Изначальная модель, которая будет содержать абсолютно все возможные предикторы

In [176]:
data.columns

Index(['author_type', 'location', 'floor', 'floors_count', 'rooms_count',
       'total_meters', 'price', 'year_of_construction', 'living_meters',
       'kitchen_meters', 'district', 'underground', 'residential_complex',
       'LAT_LON', 'LAT_LON_metro', 'metro_nearest', 'airport_nearest',
       'center_distance', 'is_developer', 'realtor', 'Метро_ботаническая',
       'Метро_геологическая', 'Метро_динамо', 'Метро_машиностроителей',
       'Метро_площадь1905года', 'Метро_проспекткосмонавтов', 'Метро_уралмаш',
       'Метро_уральская', 'Метро_чкаловская', 'Район_верх_исетский',
       'Район_железнодорожный', 'Район_кировский', 'Район_ленинский',
       'Район_октябрьский', 'Район_орджоникидзевский', 'Район_центр',
       'Район_чкаловский', 'price_per_sq_meter', 'log_center_distance',
       'is_last_floor', 'is_first_floor', 'is_residential_complex',
       'part_of_kitchen', 'part_of_living'],
      dtype='object')

In [177]:
results = smf.ols('''data.price_per_sq_meter ~ data.floor + data.floors_count + data.rooms_count
                  + data.total_meters + data.year_of_construction
                  + data.living_meters + data.kitchen_meters + data.metro_nearest
                  + data.airport_nearest + data.Метро_ботаническая
                  + data.Метро_геологическая + data.Метро_динамо + data.Метро_машиностроителей
                  + data.Метро_площадь1905года + data.Метро_проспекткосмонавтов + data.Метро_уралмаш
                  + data.Метро_уральская + data.Метро_чкаловская + data.Район_верх_исетский
                  + data.Район_железнодорожный + data.Район_кировский + data.Район_ленинский
                  + data.Район_октябрьский + data.Район_орджоникидзевский + data.Район_центр
                  + data.Район_чкаловский + data.log_center_distance
                  + data.is_last_floor + data.is_first_floor + data.is_residential_complex
                  + data.part_of_kitchen + data.part_of_living + data.is_developer + data.realtor''', data).fit()
print(results.summary())


                               OLS Regression Results                              
Dep. Variable:     data.price_per_sq_meter   R-squared:                       0.663
Model:                                 OLS   Adj. R-squared:                  0.651
Method:                      Least Squares   F-statistic:                     55.43
Date:                     Thu, 23 May 2024   Prob (F-statistic):          2.33e-194
Time:                             01:34:50   Log-Likelihood:                -11035.
No. Observations:                      964   AIC:                         2.214e+04
Df Residuals:                          930   BIC:                         2.230e+04
Df Model:                               33                                         
Covariance Type:                 nonrobust                                         
                                     coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------

Помимо наличия незначимых переменных, эта модель подвержена проблеме мультиколлинеарности

Исключим переменные living_meters (жилая площадь) и floors_count (этажность), чтобы избавиться от мультиколлинеарности.

__Вторая модель__

In [178]:
data.is_developer = data.is_developer.astype(int)

In [179]:
data.realtor = data.realtor.astype(int)

In [180]:
results = smf.ols('''data.price_per_sq_meter ~ data.floor + data.rooms_count
                  + data.total_meters + data.year_of_construction
                  + data.kitchen_meters + data.metro_nearest
                  + data.airport_nearest + data.Метро_ботаническая
                  + data.Метро_геологическая + data.Метро_динамо + data.Метро_машиностроителей
                  + data.Метро_площадь1905года + data.Метро_проспекткосмонавтов + data.Метро_уралмаш
                  + data.Метро_уральская + data.Метро_чкаловская + data.Район_верх_исетский
                  + data.Район_железнодорожный + data.Район_кировский + data.Район_ленинский
                  + data.Район_октябрьский + data.Район_орджоникидзевский + data.Район_центр
                  + data.Район_чкаловский + data.log_center_distance
                  + data.is_last_floor + data.is_first_floor + data.is_residential_complex
                  + data.part_of_kitchen + data.part_of_living + data.is_developer + data.realtor''', data).fit()
print(results.summary())


                               OLS Regression Results                              
Dep. Variable:     data.price_per_sq_meter   R-squared:                       0.658
Model:                                 OLS   Adj. R-squared:                  0.647
Method:                      Least Squares   F-statistic:                     57.82
Date:                     Thu, 23 May 2024   Prob (F-statistic):          3.51e-193
Time:                             01:34:50   Log-Likelihood:                -11042.
No. Observations:                      964   AIC:                         2.215e+04
Df Residuals:                          932   BIC:                         2.230e+04
Df Model:                               31                                         
Covariance Type:                 nonrobust                                         
                                     coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------

Сделаем VIF тест для проверки модели на наличие мультиколлинеарности.

In [181]:
from patsy import dmatrices
from statsmodels.stats.outliers_influence import variance_inflation_factor

#find design matrix for linear regression model using 'rating' as response variable 
y, X = dmatrices(get_regression_equation([
     'floor',
     'rooms_count',
     'total_meters',
     'year_of_construction',
     'kitchen_meters',
     'metro_nearest',
     'airport_nearest',
     'Метро_ботаническая',
     'Метро_динамо',
     'Метро_машиностроителей',
     'Метро_площадь1905года',
     'Метро_проспекткосмонавтов',
     'Метро_уралмаш',
     'Метро_уральская',
     'Метро_чкаловская',
     'Район_железнодорожный',
     'Район_кировский',
     'Район_орджоникидзевский',
     'Район_чкаловский',
     'Район_ленинский',
     'Район_октябрьский',
     'Район_центр',
     'log_center_distance',
     'is_last_floor',
     'is_first_floor',
     'is_residential_complex',
     'is_developer',
     'realtor',
     'part_of_kitchen',
     'part_of_living']), data=data, return_type='dataframe') # удалим метро геологическая

#calculate VIF for each explanatory variable
vif = pd.DataFrame()
vif['VIF'] = [variance_inflation_factor(X.values, i) for i in range(X.shape[1])]
vif['variable'] = X.columns
vif

VIF                        variable
0   29248.670363                       Intercept
1       1.402411                      data.floor
2       5.270583                data.rooms_count
3      11.207693               data.total_meters
4       3.063054       data.year_of_construction
5      11.049725             data.kitchen_meters
6       3.065658              data.metro_nearest
7       3.775996            data.airport_nearest
8       4.082018         data.Метро_ботаническая
9       1.876846               data.Метро_динамо
10      2.085743     data.Метро_машиностроителей
11      1.400768      data.Метро_площадь1905года
12      8.481587  data.Метро_проспекткосмонавтов
13      4.196819              data.Метро_уралмаш
14      2.951523            data.Метро_уральская
15      2.780422           data.Метро_чкаловская
16      3.530365      data.Район_железнодорожный
17      3.510842            data.Район_кировский
18     10.598830    data.Район_орджоникидзевский
19      5.453118           data.Район_чкаловский
20      1.449883            data.Район_ленинский
21      2.453111          data.Район_октябрьский
22      1.534405                data.Район_центр
23      3.670751        data.log_center_distance
24      1.141263              data.is_last_floor
25      1.209807             data.is_first_floor
26      3.831891     data.is_residential_complex
27      5.548786               data.is_developer
28      3.922205                    data.realtor
29      7.574537            data.part_of_kitchen
30      2.043697             data.part_of_living

## Отбор предикторов

In [182]:
def get_regression_equation(columns):
    s = 'data.price_per_sq_meter ~ '
    for i in columns:
        s += 'data.'+i+' + '
    return s[:-3]

Посмотрим на матрицу корреляции и уберем предикторы имеющие высокий (> 0.7) коэффициент корреляции.

In [183]:
corr = data[[
     'floor',
     'rooms_count',
     'year_of_construction',
     'kitchen_meters',
     'metro_nearest',
     'airport_nearest',
     'Метро_ботаническая',
     'Метро_геологическая',
     'Метро_динамо',
     'Метро_машиностроителей',
     'Метро_площадь1905года',
     'Метро_проспекткосмонавтов',
     'Метро_уралмаш',
     'Метро_уральская',
     'Метро_чкаловская',
     'Район_верх_исетский',
     'Район_железнодорожный',
     'Район_кировский',
     'Район_ленинский',
     'Район_октябрьский',
     'Район_центр',
     'log_center_distance',
     'is_last_floor',
     'is_first_floor',
     'part_of_kitchen',
     'part_of_living']].corr()

cmap = sns.color_palette("rocket_r", as_cmap=True)

corr.style.background_gradient(cmap, axis=1)\
    .format(precision=3)\
    .set_properties(**{'max-width': '5px', 'font-size': '10pt'})\
    .set_caption("Матрица корреляции (тепловая карта)")

Построим модель, исключив незначимые переменные

In [184]:
from patsy import dmatrices
from statsmodels.stats.outliers_influence import variance_inflation_factor

#find design matrix for linear regression model using 'rating' as response variable 
y, X = dmatrices(get_regression_equation([
     'floor',
     'rooms_count',
     'year_of_construction',
     'metro_nearest',
     'Метро_ботаническая',
     'Метро_динамо',
     'Метро_машиностроителей',
     'Метро_площадь1905года',
     'Метро_проспекткосмонавтов',
     'Метро_уралмаш',
     'Метро_уральская',
     'Метро_чкаловская',
     'Район_верх_исетский',
     'Район_железнодорожный',
     'Район_кировский',
     'Район_ленинский',
     'Район_центр',
     'part_of_kitchen']), data=data, return_type='dataframe') # удалим метро геологическая

#calculate VIF for each explanatory variable
vif = pd.DataFrame()
vif['VIF'] = [variance_inflation_factor(X.values, i) for i in range(X.shape[1])]
vif['variable'] = X.columns

In [185]:
vif

VIF                        variable
0   13485.928504                       Intercept
1       1.158266                      data.floor
2       1.252120                data.rooms_count
3       1.438711       data.year_of_construction
4       1.442151              data.metro_nearest
5       2.479200         data.Метро_ботаническая
6       1.745419               data.Метро_динамо
7       1.543567     data.Метро_машиностроителей
8       1.493012      data.Метро_площадь1905года
9       1.886340  data.Метро_проспекткосмонавтов
10      1.562379              data.Метро_уралмаш
11      2.324311            data.Метро_уральская
12      2.806258           data.Метро_чкаловская
13      2.230952        data.Район_верх_исетский
14      2.393953      data.Район_железнодорожный
15      2.623163            data.Район_кировский
16      1.335453            data.Район_ленинский
17      1.478291                data.Район_центр
18      1.330015            data.part_of_kitchen

Не обнаружено коэффициента VIF > 4

## Различные модели

In [186]:
results = smf.ols(get_regression_equation([
     'floor',
     'rooms_count',
     'year_of_construction',
     'metro_nearest',
     'Метро_ботаническая',
     'Метро_динамо',
     'Метро_машиностроителей',
     'Метро_площадь1905года',
     'Метро_проспекткосмонавтов',
     'Метро_уралмаш',
     'Метро_уральская',
     'Метро_чкаловская',
     'Район_верх_исетский',
     'Район_железнодорожный',
     'Район_кировский',
     'Район_ленинский',
     'Район_центр',
     'part_of_kitchen']), data).fit()
print(results.summary())


                               OLS Regression Results                              
Dep. Variable:     data.price_per_sq_meter   R-squared:                       0.641
Model:                                 OLS   Adj. R-squared:                  0.634
Method:                      Least Squares   F-statistic:                     93.57
Date:                     Thu, 23 May 2024   Prob (F-statistic):          1.99e-195
Time:                             01:34:50   Log-Likelihood:                -11066.
No. Observations:                      964   AIC:                         2.217e+04
Df Residuals:                          945   BIC:                         2.226e+04
Df Model:                               18                                         
Covariance Type:                 nonrobust                                         
                                     coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------

В итоговой модели все коэффициенты значимы, p-value < .05

Проведем тест на гетероскедастичность:

In [187]:
from statsmodels.stats.diagnostic import het_white
white_test = het_white(results.resid , results.model.exog)

labels = ['Test Statistic', 'Test Statistic p-value', 'F-Statistic', 'F-Test p-value']

#print results of White's test
print(dict(zip(labels, white_test)))

{'Test Statistic': 254.0332907936177, 'Test Statistic p-value': 7.409862634542137e-13, 'F-Statistic': 2.6914922372017704, 'F-Test p-value': 1.0648059546531499e-15}


Низкий p-value говорит о том, что проблема гетероскедастичности имеет место. (H0: гетероскедастичности нет, p-value < 0.05 --> есть основания отвергнуть нулевую гипотезу.)

Преобразуем исходные данные - прологарифмируем зависимую переменную и некоторые предикторы.

In [188]:
data['log_price_per_sq_meter'] = data['price_per_sq_meter'].apply(math.log)

In [189]:
def get_regression_equation(columns):
    s = 'data.log_price_per_sq_meter ~ '
    for i in columns:
        s += 'data.'+i+' + '
    return s[:-3]

In [190]:
results = smf.ols(get_regression_equation([
     'floor',
     'rooms_count',
     'year_of_construction',
     'metro_nearest',
     'Метро_ботаническая',
     'Метро_динамо',
     'Метро_машиностроителей',
     'Метро_площадь1905года',
     'Метро_проспекткосмонавтов',
     'Метро_уралмаш',
     'Метро_уральская',
     'Метро_чкаловская',
     'Район_верх_исетский',
     'Район_железнодорожный',
     'Район_кировский',
     'Район_ленинский',
     'Район_центр',
     'part_of_kitchen']), data).fit()
print(results.summary())


                                 OLS Regression Results                                
Dep. Variable:     data.log_price_per_sq_meter   R-squared:                       0.677
Model:                                     OLS   Adj. R-squared:                  0.671
Method:                          Least Squares   F-statistic:                     110.2
Date:                         Thu, 23 May 2024   Prob (F-statistic):          2.24e-217
Time:                                 01:34:50   Log-Likelihood:                 427.88
No. Observations:                          964   AIC:                            -817.8
Df Residuals:                              945   BIC:                            -725.2
Df Model:                                   18                                         
Covariance Type:                     nonrobust                                         
                                     coef    std err          t      P>|t|      [0.025      0.975]
---------------------

In [191]:
from statsmodels.stats.diagnostic import het_white
white_test = het_white(results.resid , results.model.exog)

labels = ['Test Statistic', 'Test Statistic p-value', 'F-Statistic', 'F-Test p-value']

#print results of White's test
print(dict(zip(labels, white_test)))

{'Test Statistic': 187.56223008428879, 'Test Statistic p-value': 1.3231180781059006e-05, 'F-Statistic': 1.817101623798645, 'F-Test p-value': 2.325343687661081e-06}


In [192]:
cols = [
     'price_per_sq_meter',
     'metro_nearest',
     'part_of_kitchen'
]

Взаимные распределения прологарифмированных переменных

In [193]:
for i in cols[1:]:
    fig = px.scatter(y=data['price_per_sq_meter'], x=data[i].apply(math.log), trendline='ols',
                     title='График взаимного распределения цены за кв.метр и переменной '+i).show()

In [194]:
for i in cols:
    data['log_'+i] = data[i].apply(math.log)

## Итоговая модель

In [195]:
results = smf.ols(get_regression_equation([
     'floor',
     'rooms_count',
     'year_of_construction',
     'log_metro_nearest',
     'Метро_динамо',
     'Метро_машиностроителей',
     'Метро_проспекткосмонавтов',
     'Метро_уралмаш',
     'Метро_уральская',
     'Метро_чкаловская',
     'Район_верх_исетский',
     'Район_железнодорожный',
     'Район_кировский',
     'Район_центр',
     'log_part_of_kitchen']), data).fit()
print(results.summary())

                                 OLS Regression Results                                
Dep. Variable:     data.log_price_per_sq_meter   R-squared:                       0.694
Model:                                     OLS   Adj. R-squared:                  0.689
Method:                          Least Squares   F-statistic:                     143.3
Date:                         Thu, 23 May 2024   Prob (F-statistic):          2.16e-231
Time:                                 01:34:50   Log-Likelihood:                 453.44
No. Observations:                          964   AIC:                            -874.9
Df Residuals:                              948   BIC:                            -797.0
Df Model:                                   15                                         
Covariance Type:                     nonrobust                                         
                                     coef    std err          t      P>|t|      [0.025      0.975]
---------------------

In [196]:
white_test = het_white(results.resid , results.model.exog)

labels = ['Test Statistic', 'Test Statistic p-value', 'F-Statistic', 'F-Test p-value']

#print results of White's test
print(dict(zip(labels, white_test)))

{'Test Statistic': 96.74329402510347, 'Test Statistic p-value': 0.2945990944610377, 'F-Statistic': 1.0820440425290483, 'F-Test p-value': 0.2908110523000404}


p-value > 0.05 => Нет оснований отвергнуть нулевую гипотезу об отсутствии гетероскедастичности => гетероскедастичности нет.

__Итоговая модель__:

$\log(\text{Цена за квадратный метр}) = -87.5853 + 0.0025 \cdot (\text{этаж}) - 0.0654 \cdot (\text{количество комнат}) + 0.0066 \cdot (\text{Год постройки здания}) - 0.1487 \cdot \log(\text{Расстояние от метро}) - 0.0728 \cdot \text{(Метро Динамо)} - 0.1144 \cdot \text{(Метро Машиностроителей)} - 0.0841 \cdot \text{(Метро Проспект Космонавтов)} - 0.0960 \cdot \text{(Метро Уралмаш)} - 0.1564 \cdot \text{(Метро Уральская)} + 0.1112 \cdot \text{(Метро Чкаловская)} + 0.1536 \cdot \text{(Район Верх-Исетский)} + 0.1243 \cdot \text{(Район Железнодорожный)} + 0.2223 \cdot \text{(Район Кировский)} + 0.3973 \cdot \text{(Район Центральный)} + 0.0545 \cdot \text{(Доля кухни в общей площади)}$   

Где метро и район - бинарные переменные, 1 - если квартира расположена рядом с этим метро / в этом районе, иначе 0.

Исправленный коэффициент $R^2$ c штрафом на добавленные переменные составил $0.689$.

Проинтерпретируем коэффициенты финальной модели.
- Если __этаж увеличить на 1__, то цена за квадратный метр __увеличится на 2,5%__
- Если __количество комнат увеличить на 1__, то цена за квадратный метр __увеличится на 6,54%__
- Если __год постройки здания увеличить на 1__, то цена за квадратный метр __увеличится на 0,66%__
- Если __расстояние от метро увеличится на 1%__, то цена за квадратный метр __уменьшится на 0,1487%__
- Если метро __Динамо__, то цена за квадратный метр __уменьшится на 7,28%__
- Если метро __Машиностроителей__, то цена за квадратный метр __уменьшится на 11,44%__
- Если метро __Проспект Космонавтов__, то цена за квадратный метр __уменьшится на 8,41%__
- Если метро __Уралмаш__, то цена за квадратный метр __уменьшится на 9,6%__
- Если метро __Уральская__, то цена за квадратный метр __уменьшится на 15,64%__
- Если метро __Чкаловская__, то цена за квадратный метр __увеличится на 11,12%__
- Если район __Верх-Исетский__, то цена за квадратный метр __увеличится на 15,36%__
- Если район __Железнодорожный__, то цена за квадратный метр __увеличится на 12,36%__
- Если район __Кировский__, то цена за квадратный метр __увеличится на 22,23%__
- Если район __Центр__, то цена за квадратный метр __увеличится на 39,73%__
- Если __доля кухни в общей площади увеличится на 1__, то цена за квадратный метр __увеличится на 5,45%__
